In [7]:
import numpy as np
import os
import matplotlib.pyplot as plt
import h5py
import sys
from scipy.interpolate import RegularGridInterpolator
import plotly.graph_objects as go
np.set_printoptions(precision=6, suppress=True, threshold=sys.maxsize)

print(os.getcwd())

/home/chn/repo/SiC-2nd-paper


In [ ]:
res = 100
frequency = [[[None for _ in range(res + 1)] for _ in range(res + 1)] for _ in range(24)]
center_freq = [
  0, 0, 0,
  5.715, 5.715, 5.935, 5.935, 7.720, 7.720, # E2-1 E2-2 E1-1
  11.698, 11.924, 17.751, # B1-1 B1-2 A1-1
  22.407, 22.407, 22.687, 22.687, 22.929, 22.929, # E1-2 E2-3 E2-4
  23.297, 23.297, # normal-TO
  24.386, 26.570, 26.823, # A1-2 B1-3 B1-4
  28.014 # normal-LO
]
visible_modes = [
  3, 4, 5, 6, 7, 8, 11, # E2-1 E2-2 E1-1 A1-1
  12, 13, 14, 15, 18, 19, # E1-2 E2-3 normal-TO
  20, 23 # A1-2 normal-LO
]
negligible_polar_name = [ "E2-1", "E2-2", "E1-1", "A1-1", "E1-2", "E2-3", "A1-2"]
negligible_polar_modes = [[3, 4], [5, 6], [7, 8], [11], [12, 13], [14, 15], [20]]
negligible_polar_name = [ "E2-1", "E2-2", "E1-1", "A1-1", "E1-2", "E2-3", "normal-TO", "A1-2", "normal-LO" ]
negligible_polar_modes = [[3, 4], [5, 6], [7, 8], [11], [12, 13], [14, 15], [18, 19], [20], [23]]
for i in visible_modes:
  frequency[i] = np.loadtxt(f'../SiC-2nd/5/5.1/5.1.6/5.1.6.3/data/{i}.txt')

In [10]:
# 插值，得到不同波矢下的频率
x = np.linspace(0, 18, res + 1)
z = np.linspace(0, 18, res + 1)
light = [17.85, 10.15, 8.37]
freq_per_light = [[[None for i in range(101)] for mode in range(24)] for _ in range(len(light))]
for l in range(len(light)):
  for mode in visible_modes:
    interp = RegularGridInterpolator((z, x), frequency[mode], method='linear')
    for i in range(101):
      kx = light[l] * np.sin(i / 200 * np.pi)
      kz = light[l] * np.cos(i / 200 * np.pi)
      freq_per_light[l][mode][i] = interp((kz, kx))
for l in range(len(light)):
  fig = go.Figure()
  for mode in visible_modes:
    fig.add_trace(go.Scatter(x=np.arange(101), y=freq_per_light[0][mode], mode='lines', name=f'{mode}'))
  fig.update_layout(width=500, height=2000)
  fig.show()